In [1]:
import bs4 as bs
import datetime as dt
import os
import pandas as pd
import pandas_datareader.data as web
import pickle
import requests
import fix_yahoo_finance  #fix for yahoo data problem

In [4]:
def save_sp500_tickers():
    resp = requests.get('https://en.wikipedia.org/wiki/List_of_S%26P_500_companies')
    soup = bs.BeautifulSoup(resp.text, "html5lib") #response is .txt
    table = soup.find('table', {'class':'wikitable sortable'}) #find table to scrape
    tickers = [] # make ticker array
    for row in table.findAll('tr')[1:]: #find all tr
        ticker = row.findAll('td')[0].text #find td[0] of each row
        tickers.append(ticker) #append all you found
        
    with open("sp500tickers.pickle", "wb") as f: #write list to file
        pickle.dump(tickers, f) #write using f
        
    print(tickers)
        
    return tickers

###--------- get data from yahoo
def get_data_from_yahoo(reload_sp500=False):
    if reload_sp500:
        save_sp500_tickers()
    else:
        with open("sp500tickers.pickle", "rb") as f: #rb is read bytes
            tickers = pickle.load(f) # actually load file  
            
    if not os.path.exists('stock_dfs'): # if directory doesn't exist
        os.makedirs('stock_dfs') # make directory
        
    start = dt.datetime(2000,1,1)
    end = dt.datetime(2016,12,31)
    
    for ticker in tickers: ### this gets first 10...for ticker in tickers[:10]:
        print(ticker)
        if not os.path.exists('stock_dfs/{}.csv'.format(ticker)): # {} means 'something'
            #df = web.DataReader(ticker, 'yahoo', start, end)
            df = web.get_data_yahoo(ticker, start, end)
            df.to_csv('stock_dfs/{}.csv'.format(ticker))
        else:
            print('All ready have {}'.format(ticker))
            
def compile_data():
    with open('sp500tickers.pickle', 'rb') as f:
        tickers = pickle.load(f)
        
    main_df = pd.DataFrame()
    
    for count,ticker in enumerate(tickers): # enumerate allows you to count things
        df = pd.read_csv('stock_dfs/{}.csv'.format(ticker))
        df.set_index("Date", inplace=True)
        
        df.rename(columns = {'Adj Close': ticker}, inplace=True)
        df.drop(['Open','High','Low','Close','Volume'], 1, inplace=True)
        
        if main_df.empty:
            main_df = df
        else:
            main_df = main_df.join(df, how="outer") #how=outer when rows don't have info it saves data
            
        if count % 1 == 0: # % if remainder is 0 when divide by 10 do something
            print(count)
            print(format(ticker))
    
    print(main_df.head())
    main_df.to_csv('sp500_joined_closes.csv')
    
compile_data()

0
MMM
1
ABT
2
ABBV
3
ACN
4
ATVI
5
AYI
6
ADBE
7
AMD
8
AAP
9
AES
10
AET
11
AMG
12
AFL
13
A
14
APD
15
AKAM
16
ALK
17
ALB
18
ARE
19
ALXN
20
ALGN
21
ALLE
22
AGN
23
ADS
24
LNT
25
ALL
26
GOOGL
27
GOOG
28
MO
29
AMZN
30
AEE
31
AAL
32
AEP
33
AXP
34
AIG
35
AMT
36
AWK
37
AMP
38
ABC
39
AME
40
AMGN
41
APH
42
APC
43
ADI
44
ANSS
45
ANTM
46
AON
47
APA
48
AIV
49
AAPL
50
AMAT
51
ADM
52
ARNC
53
AJG
54
AIZ
55
T
56
ADSK
57
ADP
58
AN
59
AZO
60
AVB
61
AVY
62
BHI
63
BLL
64
BAC
65
BK
66
BCR
67
BAX
68
BBT
69
BDX
70
BBBY


KeyError: 'Date'